# MLOps로 ML 자동화하기

[tfx](https://www.tensorflow.org/tfx) 를 이용해 ml 파이프라인 컴포넌트를 구성해보고 `InteractiveContext`를 통해 인터렉티브하게 파이프라인을 실행해봅니다.


[building ml pipelines](https://learning.oreilly.com/library/view/building-machine-learning/9781492053187/) 의 내용을 정리했습니다.


In [ ]:
# requirements
! pip install -r requirements.txt

In [ ]:
import os
import tensorflow as tf
import csv
from tfx.components import CsvExampleGen, StatisticsGen
from tfx.components import ImportExampleGen
from tfx.utils.dsl_utils import external_input
from tfx.proto import example_gen_pb2
from tfx.orchestration.experimental.interactive.interactive_context import InteractiveContext

TFX의 인터렉티브 파이프라인을 사용하기 위해 아래 설정을 해줍니다.

In [2]:
context = InteractiveContext(pipeline_root='./tfx')

# 데이터

고객센터 문의 데이터를 가지고 고객이 논쟁을 벌일지 아닐지 분류해보는 ML 프로젝트를 진행합니다.

categorical 데이터와 텍스트데이터를 가지고 있는 데이터입니다.

In [3]:
import pandas as pd
pd.read_csv('./data/train/train.csv').head()

Unnamed: 0           product                  sub_product  \
0           0   Debt collection                I do not know   
1           1  Credit reporting                          NaN   
2           2   Debt collection                I do not know   
3           3          Mortgage  Conventional fixed mortgage   
4           4      Student loan     Non-federal student loan   

                                      issue  \
0           Disclosure verification of debt   
1          Improper use of my credit report   
2     Cont'd attempts collect debt not owed   
3  Loan servicing, payments, escrow account   
4        Dealing with my lender or servicer   

                                sub_issue  \
0    Right to dispute notice not received   
1         Report improperly shared by CRC   
2                        Debt is not mine   
3                                     NaN   
4  Received bad information about my loan   

                        consumer_complaint_narrative  \
0  I was denied employment because of a judgment ...   
1  I have a credit card through XXXX XXXX and XXX...   
2  Almost daily phone calls from Stellar Recovery...   
3  I submitted my monthly mortgage payment to Pri...   
4  I contacted America Education Services in XX/X...   

                        company state zip_code  \
0          Encore Capital Group    NY    113XX   
1                      Experian    IL    606XX   
2         Stellar Recovery Inc.    MI    480XX   
3  Primary Residential Mortgage    CT    066XX   
4                     AES/PHEAA    FL    321XX   

                  company_response timely_response  consumer_disputed  
0          Closed with explanation             Yes                  0  
1  Closed with non-monetary relief             Yes                  0  
2          Closed with explanation             Yes                  1  
3      Closed with monetary relief             Yes                  0  
4          Closed with explanation             Yes                  1

#  1. csv 데이터 주입하기

`data/` 에 저장되어 있는 `train.csv`와 `validation.csv`를 읽어 파이프라인에 주입합니다.

In [3]:
base_dir = os.getcwd()
data_dir = "./data"

# train, validation 디렉토리안의 파일을 읽어 각각을 train, eval 데이터로 저장되게 config를 작성합니다.
input_config = example_gen_pb2.Input(splits=[
    example_gen_pb2.Input.Split(name='train', pattern='train/*'),
    example_gen_pb2.Input.Split(name='eval', pattern='validation/*'),
])

examples = external_input(os.path.join(base_dir, data_dir))

Instructions for updating:
external_input is deprecated, directly pass the uri to ExampleGen.


In [4]:
example_gen = CsvExampleGen(input=examples, input_config=input_config)
context.run(example_gen)

ExecutionResult(
    component_id: CsvExampleGen
    execution_id: 118
    outputs:
        examples: Channel(
            type_name: Examples
            artifacts: [Artifact(artifact: id: 168
        type_id: 5
        uri: "./tfx/CsvExampleGen/examples/118"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\"]"
          }
        }
        custom_properties {
          key: "input_fingerprint"
          value {
            string_value: "split:train,num_files:1,total_bytes:66439938,xor_checksum:1602427335,sum_checksum:1602427335\nsplit:eval,num_files:1,total_bytes:12906123,xor_checksum:1602427346,sum_checksum:1602427346"
          }
        }
        custom_properties {
          key: "payload_format"
          value {
            string_value: "FORMAT_TF_EXAMPLE"
          }
        }
        custom_properties {
          key: "span"
          value {
            string_value: "0"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 5
        name: "Examples"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        properties {
          key: "version"
          value: INT
        }
        )]
        ))

# outputs

config 설정대로 `train`, `eval` 로 데이터가 TFRecord 형식으로 주입되었습니다.

In [6]:
! ls ./tfx/CsvExampleGen/examples/1/

eval  train


In [5]:
! ls ./tfx/CsvExampleGen/examples/1/train

data_tfrecord-00000-of-00001.gz


# 2. TFRecord 파일 주입

csv 파일을 tfrecord로 변환한 후 tfx를 이용해 파이프라인에 주입합니다.

In [8]:
def _bytes_feature(value):
    return tf.train.Feature(bytes_list=tf.train.BytesList(value=[value.encode()]))

def _float_feature(value):
    return tf.train.Feature(float_list=tf.train.FloatList(value=[value]))

def _int64_feature(value):
    return tf.train.Feature(int64_list=tf.train.Int64List(value=[value]))


original_data_file = os.path.join(
    "consumer_complaints_with_narrative.csv")
tfrecord_filename = "./tfrecord/consumer-complaints.tfrecord"
tf_record_writer = tf.io.TFRecordWriter(tfrecord_filename) 

with open(original_data_file) as csv_file:
    reader = csv.DictReader(csv_file, delimiter=",", quotechar='"')
    for row in reader:
        example = tf.train.Example(features=tf.train.Features(feature={ 
            "product": _bytes_feature((row["product"])),
            "sub_product": _bytes_feature(row["sub_product"]),
            "issue": _bytes_feature(row["issue"]),
            "sub_issue": _bytes_feature(row["sub_issue"]),
            "state": _bytes_feature(row["state"]),
            "company": _bytes_feature(row["company"]),
            "company_response": _bytes_feature(row["company_response"]),
            "consumer_complaint_narrative": \
                _bytes_feature(row["consumer_complaint_narrative"]),
            "timely_response": _bytes_feature(row["timely_response"]),
            "consumer_disputed": _bytes_feature(row["consumer_disputed"]),
        }))
        tf_record_writer.write(example.SerializeToString()) 
    tf_record_writer.close()

In [9]:
!ls tfrecord

consumer-complaints.tfrecord


# tfrecord 주입

In [6]:
data_dir = "./tfrecord"
examples = external_input(data_dir)
example_gen = ImportExampleGen(input=examples)

context.run(example_gen)

ExecutionResult(
    component_id: ImportExampleGen
    execution_id: 59
    outputs:
        examples: Channel(
            type_name: Examples
            artifacts: [Artifact(artifact: id: 82
        type_id: 5
        uri: "./tfx/ImportExampleGen/examples/59"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\"]"
          }
        }
        custom_properties {
          key: "input_fingerprint"
          value {
            string_value: "split:single_split,num_files:1,total_bytes:93893875,xor_checksum:1602677397,sum_checksum:1602677397"
          }
        }
        custom_properties {
          key: "payload_format"
          value {
            string_value: "FORMAT_TF_EXAMPLE"
          }
        }
        custom_properties {
          key: "span"
          value {
            string_value: "0"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 5
        name: "Examples"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        properties {
          key: "version"
          value: INT
        }
        )]
        ))

# 데이터 분리

저장된 데이터가 분리되어 있지 않아도 데이터 주입 컴포넌트를 이용해 분리 후 주입할 수 있습니다.

데이터를 `SplitConfig`를 이용해 `train`, `eval`, `test`로 6:2:2 비율로 나누어 분리합니다

In [ ]:
base_dir = os.getcwd()
data_dir = "data/train"

output_config = example_gen_pb2.Output(
    split_config=example_gen_pb2.SplitConfig(splits=[ 
        example_gen_pb2.SplitConfig.Split(name='train', hash_buckets=6), 
        example_gen_pb2.SplitConfig.Split(name='eval', hash_buckets=2),
        example_gen_pb2.SplitConfig.Split(name='test', hash_buckets=2)
    ]))

In [11]:
examples = external_input(os.path.join(base_dir, data_dir))
example_gen = CsvExampleGen(input=examples, output_config=output_config) 

context.run(example_gen)

ExecutionResult(
    component_id: CsvExampleGen
    execution_id: 16
    outputs:
        examples: Channel(
            type_name: Examples
            artifacts: [Artifact(artifact: id: 18
        type_id: 5
        uri: "./tfx/CsvExampleGen/examples/16"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\", \"test\"]"
          }
        }
        custom_properties {
          key: "input_fingerprint"
          value {
            string_value: "split:single_split,num_files:1,total_bytes:66439938,xor_checksum:1602427335,sum_checksum:1602427335"
          }
        }
        custom_properties {
          key: "payload_format"
          value {
            string_value: "FORMAT_TF_EXAMPLE"
          }
        }
        custom_properties {
          key: "span"
          value {
            string_value: "0"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 5
        name: "Examples"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        properties {
          key: "version"
          value: INT
        }
        )]
        ))

# Data Validatoin

### 1. tensorflow_data_validation 에서 사용하기

TFDV를 이용해 데이터를 읽고 분석해봅니다.

In [7]:
import tensorflow_data_validation as tfdv

CSV 파일 읽기

In [8]:
stats = tfdv.generate_statistics_from_csv(
    data_location='./data//train/train.csv',
    delimiter=',')

Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


TFRecord 파일 읽기

In [14]:
stats = tfdv.generate_statistics_from_tfrecord(
    data_location='/data/###.tfrecord')

OSError: No files found based on the file pattern /data/###.tfrecord

# 스키마 생성

tfdv를 이용해 현재 데이터를 바탕으로 스키마를 추론합니다.

In [9]:
schema = tfdv.infer_schema(stats)

In [10]:
tfdv.display_schema(schema)

Type  Presence Valency              Domain
Feature name                                                                
'product'                       STRING  required                   'product'
'sub_product'                   STRING  optional  single       'sub_product'
'issue'                         STRING  required                     'issue'
'sub_issue'                     STRING  optional  single         'sub_issue'
'consumer_complaint_narrative'   BYTES  required                           -
'company'                        BYTES  required                           -
'state'                         STRING  optional  single             'state'
'zip_code'                       BYTES  optional  single                   -
'company_response'              STRING  required          'company_response'
'timely_response'               STRING  required           'timely_response'
''                                 INT  required                           -
'consumer_disputed'                INT  required                           -

/home/juhyung/anaconda3/envs/pipe/lib/python3.6/site-packages/tensorflow_data_validation/utils/display_util.py:138: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  pd.set_option('max_colwidth', -1)


Values
Domain                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             
'product'           'Bank account or service', 'Consumer Loan', 'Credit card', 'Credit reporting', 'Debt collection', 'Money transfers', 'Mortgage', 'Other financial service', 'Payday loan', 'Prepaid card', 'Student loan'                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        

# 데이터셋 비교

train 데이터와 validation 데이터의 분포를 확인합니다.

In [11]:
train_stats = tfdv.generate_statistics_from_csv(
    data_location='./data//train/train.csv')
val_stats = tfdv.generate_statistics_from_csv(
    data_location='./data/validation/validation.csv')

tfdv.visualize_statistics(lhs_statistics=val_stats, rhs_statistics=train_stats,
                          lhs_name='VAL_DATASET', rhs_name='TRAIN_DATASET')

In [18]:
anomalies = tfdv.validate_statistics(statistics=val_stats, schema=schema)
tfdv.display_anomalies(anomalies)

# 스키마 업데이트

tfdv는 인풋 데이터를 가지고 스키마를 추론하기에 스키마가 정확하지 않을 수 있습니다.
그럴때 스키마를 직접 업데이트 합니다.

In [19]:
schema = tfdv.load_schema_text(schema_location)

NameError: name 'schema_location' is not defined

In [20]:
# sub_issue 의 min_fraction을 0.9로 변경
sub_issue_feature = tfdv.get_feature(schema, 'sub_issue')
sub_issue_feature.presence.min_fraction = 0.9

In [21]:
# state에서 AK 제거
state_domain = tfdv.get_domain(schema, 'state')
state_domain.value.remove('AK')

In [22]:
tfdv.write_schema_text(schema, './schema')

# 데이터 Skew, Drift

두 데이터가 비슷한 데이터인지 검사합니다.

보통 train, validation 데이터는 데이터의 skew 를 검사하고

과거와 현재 데이터는 drift를 검사합니다.


1. data skew
- 두 데이터 분포의 큰 차이점을 감지
- TFDV에서는 L-infinity norm을 이용해 감지한다.
2. data drift
- 과거와 현재 데이터의 분포가 변했는가를 감지한다.

# skew

train과 validation 데이터를 비교

In [23]:
tfdv.get_feature(schema,
                 'company').skew_comparator.infinity_norm.threshold = 0.01

skew_anomalies = tfdv.validate_statistics(statistics=train_stats,
                                          schema=schema,
                                          # 비교하려는 데이터
                                          serving_statistics=val_stats)

In [24]:
tfdv.display_anomalies(skew_anomalies)

/home/juhyung/anaconda3/envs/pipe/lib/python3.6/site-packages/tensorflow_data_validation/utils/display_util.py:173: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  pd.set_option('max_colwidth', -1)


Anomaly short description  \
Feature name                             
'sub_issue'   Column dropped             
'state'       Unexpected string values   

                                                 Anomaly long description  
Feature name                                                               
'sub_issue'   The feature was present in fewer examples than expected.     
'state'       Examples contain values missing from the schema: AK (<1%).

# drift
과거와 현재 데이터를 비교

In [25]:
tfdv.get_feature(schema,
                 'company').drift_comparator.infinity_norm.threshold = 0.01
drift_anomalies = tfdv.validate_statistics(statistics=train_stats_today,
                                           schema=schema,
                                           previous_statistics=\
                                               train_stats_yesterday)

NameError: name 'train_stats_today' is not defined

# 2. TFX 데이터 검증 컴포넌트 사용하기

In [5]:
from tfx.components import StatisticsGen, SchemaGen

# 데이터 분석

In [6]:
statistics_gen = StatisticsGen(
    examples=example_gen.outputs['examples'])
context.run(statistics_gen)

ExecutionResult(
    component_id: StatisticsGen
    execution_id: 119
    outputs:
        statistics: Channel(
            type_name: ExampleStatistics
            artifacts: [Artifact(artifact: id: 169
        type_id: 8
        uri: "./tfx/StatisticsGen/statistics/119"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\"]"
          }
        }
        custom_properties {
          key: "name"
          value {
            string_value: "statistics"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "StatisticsGen"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 8
        name: "ExampleStatistics"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        )]
        ))

In [7]:
context.show(statistics_gen.outputs['statistics'])

Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


# 스키마 생성

In [8]:
schema_gen = SchemaGen(
    statistics=statistics_gen.outputs['statistics'],
    infer_feature_shape=True)

context.run(schema_gen)

ExecutionResult(
    component_id: SchemaGen
    execution_id: 120
    outputs:
        schema: Channel(
            type_name: Schema
            artifacts: [Artifact(artifact: id: 170
        type_id: 10
        uri: "./tfx/SchemaGen/schema/120"
        custom_properties {
          key: "name"
          value {
            string_value: "schema"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "SchemaGen"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 10
        name: "Schema"
        )]
        ))

In [9]:
context.show(schema_gen.outputs['schema'])

Type  Presence Valency              Domain
Feature name                                                                
'company'                        BYTES  required                           -
'company_response'              STRING  required          'company_response'
'consumer_complaint_narrative'   BYTES  required                           -
'issue'                         STRING  required                     'issue'
'product'                       STRING  required                   'product'
'state'                         STRING  required                     'state'
'sub_issue'                     STRING  required                 'sub_issue'
'sub_product'                   STRING  required               'sub_product'
'timely_response'               STRING  required           'timely_response'
'zip_code'                       BYTES  required                           -
''                                 INT  required                           -
'consumer_disputed'                INT  required                           -

/home/juhyung/anaconda3/envs/pipe/lib/python3.6/site-packages/tensorflow_data_validation/utils/display_util.py:138: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  pd.set_option('max_colwidth', -1)


Values
Domain                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             
'company_response'  'Closed', 'Closed with explanation', 'Closed with monetary relief', 'Closed with non-monetary relief', 'Untimely response'                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

# 데이터 검증

In [9]:
from tfx.components import ExampleValidator

In [10]:
example_validator = ExampleValidator(
    statistics=statistics_gen.outputs['statistics'],
    schema=schema_gen.outputs['schema'])
context.run(example_validator)

ExecutionResult(
    component_id: ExampleValidator
    execution_id: 121
    outputs:
        anomalies: Channel(
            type_name: ExampleAnomalies
            artifacts: [Artifact(artifact: id: 171
        type_id: 12
        uri: "./tfx/ExampleValidator/anomalies/121"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\"]"
          }
        }
        custom_properties {
          key: "name"
          value {
            string_value: "anomalies"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "ExampleValidator"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 12
        name: "ExampleAnomalies"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        )]
        ))

In [33]:
context.show(example_validator.outputs['anomalies'])

# 데이터 전처리

tf 함수를 이용해 전처리를 처리하는 전처리 그래프를 만듭니다.

In [11]:
import tensorflow_transform as tft
from tfx.components import Transform
from module import *

In [12]:
transform = Transform(
    examples=example_gen.outputs['examples'],
    schema=schema_gen.outputs['schema'],
    module_file=os.path.abspath("module/transform.py"))
context.run(transform)

Instructions for updating:
Schema is a deprecated, use schema_utils.schema_from_feature_spec to create a `Schema`
Instructions for updating:
Use ref() instead.


Instructions for updating:
This function will only be available through the v1 compatibility library as tf.compat.v1.saved_model.utils.build_tensor_info or tf.compat.v1.saved_model.build_tensor_info.
INFO:tensorflow:Assets added to graph.
INFO:tensorflow:No assets to write.
Type is unsupported, or the types of the items don't match field type in CollectionDef. Note this is a warning and probably safe to ignore.
'Counter' object has no attribute 'name'
INFO:tensorflow:SavedModel written to: ./tfx/Transform/transform_graph/122/.temp_path/tftransform_tmp/4f5d793461bf484a902efad81b6dbd4f/saved_model.pb
INFO:tensorflow:Assets added to graph.
INFO:tensorflow:No assets to write.
Type is unsupported, or the types of the items don't match field type in CollectionDef. Note this is a warning and probably safe to ignore.
'Counter' object has no attribute 'name'
INFO:tensorflow:SavedModel written to: ./tfx/Transform/transform_graph/122/.temp_path/tftransform_tmp/0d255755f9924ad2ba8a3a2b8aa223c5/sav

INFO:tensorflow:Saver not created because there are no variables in the graph to restore
INFO:tensorflow:Saver not created because there are no variables in the graph to restore
INFO:tensorflow:Assets added to graph.
INFO:tensorflow:Assets written to: ./tfx/Transform/transform_graph/122/.temp_path/tftransform_tmp/c905803ae7ef46a5b426d2f64caf7b49/assets
INFO:tensorflow:SavedModel written to: ./tfx/Transform/transform_graph/122/.temp_path/tftransform_tmp/c905803ae7ef46a5b426d2f64caf7b49/saved_model.pb
value: "\n\013\n\tConst_1:0\022-vocab_compute_and_apply_vocabulary_vocabulary"

value: "\n\013\n\tConst_3:0\022/vocab_compute_and_apply_vocabulary_1_vocabulary"

value: "\n\013\n\tConst_5:0\022/vocab_compute_and_apply_vocabulary_2_vocabulary"

value: "\n\013\n\tConst_7:0\022/vocab_compute_and_apply_vocabulary_3_vocabulary"

value: "\n\013\n\tConst_9:0\022/vocab_compute_and_apply_vocabulary_4_vocabulary"

INFO:tensorflow:Saver not created because there are no variables in the graph to restor

ExecutionResult(
    component_id: Transform
    execution_id: 122
    outputs:
        transform_graph: Channel(
            type_name: TransformGraph
            artifacts: [Artifact(artifact: id: 172
        type_id: 14
        uri: "./tfx/Transform/transform_graph/122"
        custom_properties {
          key: "name"
          value {
            string_value: "transform_graph"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "Transform"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 14
        name: "TransformGraph"
        )]
        )
        transformed_examples: Channel(
            type_name: Examples
            artifacts: [Artifact(artifact: id: 173
        type_id: 5
        uri: "./tfx/Transform/transformed_examples/122"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\"]"
          }
        }
        custom_properties {
          key: "name"
          value {
            string_value: "transformed_examples"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "Transform"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 5
        name: "Examples"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        properties {
          key: "version"
          value: INT
        }
        )]
        )
        updated_analyzer_cache: Channel(
            type_name: TransformCache
            artifacts: [Artifact(artifact: id: 174
        type_id: 15
        uri: "./tfx/Transform/updated_analyzer_cache/122"
        custom_properties {
          key: "name"
          value {
            string_value: "updated_analyzer_cache"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "Transform"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 15
        name: "TransformCache"
        )]
        ))

## 이미지 전처리 예시

In [16]:
def process_image(raw_image):
    raw_image = tf.reshape(raw_image, [-1])
    img_rgb = tf.io.decode_jpeg(raw_image, channels=3) 
    img_gray = tf.image.rgb_to_grayscale(img_rgb) 
    img = tf.image.convert_image_dtype(img, tf.float32)
    resized_img = tf.image.resize_with_pad( 
        img,
        target_height=300,
        target_width=300
    )
    img_grayscale = tf.image.rgb_to_grayscale(resized_img) 
    return tf.reshape(img_grayscale, [-1, 300, 300, 1])

# 모델 학습

module.py 에 구현된 `run_fn()` 함수를 이용해 학습 컴포넌트를 진행한다.

학습 데이터는 전처리 컴포넌트의 아웃풋인 `transformed_examples`를 사용한다.

savedModel 저장시 서빙에 쓸 전처리 그래프인 `transformed_graph`도 넣는다.

In [13]:
from tfx.components import Trainer
from tfx.components.base import executor_spec
from tfx.components.trainer.executor import GenericExecutor
from tfx.proto import trainer_pb2
from keras_trainer import *

In [14]:
TRAINING_STEPS = 100
EVALUATION_STEPS = 10

trainer = Trainer(
    module_file=os.path.abspath("module/keras_trainer.py"),
    custom_executor_spec=executor_spec.ExecutorClassSpec(GenericExecutor),
    transformed_examples=transform.outputs['transformed_examples'],
    transform_graph=transform.outputs['transform_graph'],
    schema=schema_gen.outputs['schema'],
    train_args=trainer_pb2.TrainArgs(num_steps=TRAINING_STEPS),
    eval_args=trainer_pb2.EvalArgs(num_steps=EVALUATION_STEPS))

In [15]:
context.run(trainer)

Model: "functional_1"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
consumer_complaint_narrative_xf [(None, 1)]          0                                            
__________________________________________________________________________________________________
tf_op_layer_Reshape (TensorFlow [(None,)]            0           consumer_complaint_narrative_xf[0
__________________________________________________________________________________________________
keras_layer (KerasLayer)        (None, 512)          256797824   tf_op_layer_Reshape[0][0]        
__________________________________________________________________________________________________
reshape (Reshape)               (None, 512)          0           keras_layer[0][0]                
_______________________________________________________________________________________

ExecutionResult(
    component_id: Trainer
    execution_id: 123
    outputs:
        model: Channel(
            type_name: Model
            artifacts: [Artifact(artifact: id: 175
        type_id: 17
        uri: "./tfx/Trainer/model/123"
        custom_properties {
          key: "name"
          value {
            string_value: "model"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "Trainer"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 17
        name: "Model"
        )]
        )
        model_run: Channel(
            type_name: ModelRun
            artifacts: [Artifact(artifact: id: 176
        type_id: 18
        uri: "./tfx/Trainer/model_run/123"
        custom_properties {
          key: "name"
          value {
            string_value: "model_run"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "Trainer"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 18
        name: "ModelRun"
        )]
        ))

# 모델 검증

# 1. TFMA 써보기

저장되어 있는 savedModel을 분석, 성능 비교한다.

In [16]:
import tensorflow_model_analysis as tfma

In [17]:
eval_shared_model = tfma.default_eval_shared_model(
    eval_saved_model_path='tfx/Trainer/model/84/serving_model_dir/',
    tags=[tf.saved_model.SERVING])

In [18]:
eval_config=tfma.EvalConfig(
    model_specs=[tfma.ModelSpec(label_key='consumer_disputed')],
    slicing_specs=[tfma.SlicingSpec()],
    metrics_specs=[
        tfma.MetricsSpec(metrics=[
            tfma.MetricConfig(class_name='BinaryAccuracy'),
            tfma.MetricConfig(class_name='ExampleCount'),
            tfma.MetricConfig(class_name='FalsePositives'),
            tfma.MetricConfig(class_name='TruePositives'),
            tfma.MetricConfig(class_name='FalseNegatives'),
            tfma.MetricConfig(class_name='TrueNegatives')
        ])
    ]
)

In [ ]:
eval_result = tfma.run_model_analysis(
    eval_shared_model=eval_shared_model,
    eval_config=eval_config,
    data_location=_VAL_DATA_LOCATION,
    output_path='result',
    file_format='tfrecords')

tfma.view.render_slicing_metrics(eval_result)

# 2. TFX 에서 TFMA 사용하기

TFX를 이용해 학습 컴포넌트의 결과물을 분석하고 성능을 비교한다.

이전 모델보다 성능이 좋아졌다면 그 모델은 blessing 이 된다.

In [19]:
from tfx.components import ResolverNode
from tfx.dsl.experimental import latest_blessed_model_resolver
from tfx.types import Channel
from tfx.types.standard_artifacts import Model
from tfx.types.standard_artifacts import ModelBlessing

In [20]:
model_resolver = ResolverNode(
    instance_name='latest_blessed_model_resolver',
    resolver_class=latest_blessed_model_resolver.LatestBlessedModelResolver,
    model=Channel(type=Model),
    model_blessing=Channel(type=ModelBlessing)
)
context.run(model_resolver)

ExecutionResult(
    component_id: ResolverNode.latest_blessed_model_resolver
    execution_id: 124
    outputs:
        model: Channel(
            type_name: Model
            artifacts: []
        )
        model_blessing: Channel(
            type_name: ModelBlessing
            artifacts: []
        ))

In [21]:
import tensorflow_model_analysis as tfma

eval_config=tfma.EvalConfig(
    model_specs=[tfma.ModelSpec(label_key='consumer_disputed')],
    slicing_specs=[tfma.SlicingSpec(),
                   tfma.SlicingSpec(feature_keys=['product'])],
    metrics_specs=[
        tfma.MetricsSpec(metrics=[
            tfma.MetricConfig(class_name='BinaryAccuracy'),
            tfma.MetricConfig(class_name='ExampleCount'),
            tfma.MetricConfig(class_name='AUC')
        ])
    ]
)

In [22]:
from tfx.components import Evaluator

evaluator = Evaluator(
    examples=example_gen.outputs['examples'],
    model=trainer.outputs['model'],
    baseline_model=model_resolver.outputs['model'],
    eval_config=eval_config
)
context.run(evaluator)

ExecutionResult(
    component_id: Evaluator
    execution_id: 125
    outputs:
        evaluation: Channel(
            type_name: ModelEvaluation
            artifacts: [Artifact(artifact: id: 177
        type_id: 21
        uri: "./tfx/Evaluator/evaluation/125"
        custom_properties {
          key: "name"
          value {
            string_value: "evaluation"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "Evaluator"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 21
        name: "ModelEvaluation"
        )]
        )
        blessing: Channel(
            type_name: ModelBlessing
            artifacts: [Artifact(artifact: id: 178
        type_id: 22
        uri: "./tfx/Evaluator/blessing/125"
        custom_properties {
          key: "name"
          value {
            string_value: "blessing"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "Evaluator"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 22
        name: "ModelBlessing"
        )]
        ))

In [29]:
eval_result = evaluator.outputs['evaluation'].get()[0].uri
tfma_result = tfma.load_eval_result(eval_result)
tfma.addons.fairness.view.widget_view.render_fairness_indicator(tfma_result)

FairnessIndicatorViewer(slicingMetrics=[{'sliceValue': 'Overall', 'slice': 'Overall', 'metrics': {'auc': {'dou…

In [24]:
tfma.addons.fairness.view.widget_view.render_fairness_indicator(tfma_result)

FairnessIndicatorViewer(slicingMetrics=[{'sliceValue': 'Overall', 'slice': 'Overall', 'metrics': {'auc': {'dou…

In [ ]:
eval_config=tfma.EvalConfig(
    model_specs=[tfma.ModelSpec(label_key='consumer_disputed')],
    slicing_specs=[tfma.SlicingSpec(),
                   tfma.SlicingSpec(feature_keys=['product'])],
    metrics_specs=[
        tfma.MetricsSpec(
            metrics=[
                tfma.MetricConfig(class_name='BinaryAccuracy'),
                tfma.MetricConfig(class_name='ExampleCount'),
                tfma.MetricConfig(class_name='AUC')
            ],
            thresholds={
                'AUC':
                    tfma.config.MetricThreshold(
                        value_threshold=tfma.GenericValueThreshold(
                            lower_bound={'value': 0.65}),
                        change_threshold=tfma.GenericChangeThreshold(
                            direction=tfma.MetricDirection.HIGHER_IS_BETTER,
                            absolute={'value': 0.01}
                        )
                    )
            }
        )
    ]
)

In [27]:
eval_result = evaluator.outputs['evaluation'].get()[0].uri
print(tfma.load_validation_result(eval_result))

validation_ok: true



# Pusher

검증된 모델을 서빙서버에 업데이트 한다.

In [30]:
from tfx.components import Pusher
from tfx.proto import pusher_pb2

_serving_model_dir = "serving_model_dir"

pusher = Pusher(
    model=trainer.outputs['model'],
    model_blessing=evaluator.outputs['blessing'],
    push_destination=pusher_pb2.PushDestination(
        filesystem=pusher_pb2.PushDestination.Filesystem(
            base_directory=_serving_model_dir)))
context.run(pusher)

ExecutionResult(
    component_id: Pusher
    execution_id: 126
    outputs:
        pushed_model: Channel(
            type_name: PushedModel
            artifacts: [Artifact(artifact: id: 179
        type_id: 24
        uri: "./tfx/Pusher/pushed_model/126"
        custom_properties {
          key: "name"
          value {
            string_value: "pushed_model"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "Pusher"
          }
        }
        custom_properties {
          key: "pushed"
          value {
            int_value: 0
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 24
        name: "PushedModel"
        )]
        ))